<a href="https://colab.research.google.com/github/FreddyEB/Artificial_Intelligence_T1/blob/master/AI_Tarea1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
#dataset y repo
#!git clone https://github.com/jmsaavedrar/machine_learning
#!wget -O MNIST-5000.zip https://www.dropbox.com/scl/fi/tvrvsl2nd7e1upcmazgm1/MNIST-5000.zip?rlkey=j5a7rauyg83p0x6ybltev9pgj&e=1&st=bz50c9jf&dl=1

--2024-08-18 20:24:07--  https://www.dropbox.com/scl/fi/tvrvsl2nd7e1upcmazgm1/MNIST-5000.zip?rlkey=j5a7rauyg83p0x6ybltev9pgj
Resolving www.dropbox.com (www.dropbox.com)... 162.125.4.18, 2620:100:6057:18::a27d:d12
Connecting to www.dropbox.com (www.dropbox.com)|162.125.4.18|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://uc13701746f5f9354f5fcf5edf1d.dl.dropboxusercontent.com/cd/0/inline/CY4PSb8abvCtt-sFtCRwswvkST9ix-s4XM0vpKZr68SRL4kz55WyOoe6UbKAO7CDhg2e-4c-Rcd_Q3ERQfAh6Tpd-e3Id0pqL2f6vFy-6HTtgmTwWg6Hr0_6nLsbixOGcx29JcrJPFShgvvT7GX7MMAi/file# [following]
--2024-08-18 20:24:07--  https://uc13701746f5f9354f5fcf5edf1d.dl.dropboxusercontent.com/cd/0/inline/CY4PSb8abvCtt-sFtCRwswvkST9ix-s4XM0vpKZr68SRL4kz55WyOoe6UbKAO7CDhg2e-4c-Rcd_Q3ERQfAh6Tpd-e3Id0pqL2f6vFy-6HTtgmTwWg6Hr0_6nLsbixOGcx29JcrJPFShgvvT7GX7MMAi/file
Resolving uc13701746f5f9354f5fcf5edf1d.dl.dropboxusercontent.com (uc13701746f5f9354f5fcf5edf1d.dl.dropboxusercontent.com)... 162.125.4.15, 2620

In [93]:
from google.colab import drive
import os
import cv2
import pandas as pd
import tensorflow as tf
import numpy as np
import matplotlib.pyplot as plt
from skimage.io import imread, imshow
from skimage.feature import hog
from skimage import exposure
from tensorflow.keras.models import load_model
import tensorflow.keras.datasets as datasets
from keras.layers import TFSMLayer
from tensorflow.keras.preprocessing import image

#drive.mount('/content/drive')

In [94]:
import zipfile
# extracción de la info del drive
zip_path = '/content/drive/MyDrive/AI_Data/Data.zip'
extract_path = '/content/data/'
os.makedirs(extract_path, exist_ok=True)
with zipfile.ZipFile(zip_path) as zf:
    zf.extractall(extract_path)
os.listdir(extract_path)

['__MACOSX', 'MNIST-5000', 'mnist_model']

In [ ]:
# para ver la correcta extracción de la info del drive
train_images_path = '/content/data/MNIST-5000/train_images'
valid_images_path = '/content/data/MNIST-5000/valid_images'

def load_images_from_directory(directory):
    images = []
    for filename in os.listdir(directory):
        img_path = os.path.join(directory, filename)
        img = image.load_img(img_path, color_mode='grayscale', target_size=(28, 28))
        img_array = image.img_to_array(img)
        images.append(img_array)
    return np.array(images)

train_images = load_images_from_directory(train_images_path)
valid_images = load_images_from_directory(valid_images_path)

train_images = train_images.squeeze().astype('uint8')
valid_images = valid_images.squeeze().astype('uint8')

print(f'Train Images: {train_images.shape}')
print(f'Valid Images: {valid_images.shape}')

fig, axs = plt.subplots(1, 5, figsize=(15, 3))
for i in range(5):
    axs[i].imshow(train_images[i], cmap='gray')
    axs[i].axis('off')
plt.show()

fig, axs = plt.subplots(1, 5, figsize=(15, 3))
for i in range(5):
    axs[i].imshow(valid_images[i], cmap='gray')
    axs[i].axis('off')
plt.show()

# Flatten

In [140]:
def get_data_train(path):
    datas = []
    for image_path in os.listdir(path):
        data = {}
        data["x"] = cv2.imread(os.path.join(path, image_path), cv2.IMREAD_GRAYSCALE)
        data["x"] = data["x"].flatten()
        data["y"] = image_path.split("_")[-1][:-4]
        datas.append(data)
    return datas

In [142]:
train = get_data_train("/content/data/MNIST-5000/train_images")
train

[{'x': array([255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255,

In [143]:
def get_data_valid(path):
  datas_valid=[]
  for image_path in os.listdir(path):
    data = {}
    data["x"] = cv2.imread(os.path.join(path, image_path), cv2.IMREAD_GRAYSCALE)
    data["x"] = data["x"].flatten()
    data["y"] = image_path.split("_")[-1][:-4]
    datas_valid.append(data)
  return datas_valid

In [144]:
valid = get_data_valid("/content/data/MNIST-5000/valid_images")
valid

[{'x': array([255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,   0,
           0, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255,   0,   0, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255,   0,   0, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255,   0,   0, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255, 255,   0,   0, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255, 255,
         255, 255, 255, 255, 255,

In [145]:
x_train = np.array([data["x"] for data in train])
y_train = np.array([data["y"] for data in train]).astype(np.float32)
x_valid = np.array([data["x"] for data in valid])
y_valid = np.array([data["y"] for data in valid]).astype(np.float32)

# train
print(x_train.dtype)
print(type(x_train))
print(y_train.dtype)
print((y_train))
#valid
print(x_valid.dtype)
print(type(x_valid))
print(y_valid.dtype)
print((y_valid))

uint8
<class 'numpy.ndarray'>
float32
[8. 0. 3. ... 9. 2. 2.]
uint8
<class 'numpy.ndarray'>
float32
[6. 4. 4. 8. 7. 5. 3. 1. 9. 2. 2. 2. 7. 9. 4. 1. 6. 8. 3. 5. 9. 1. 5. 5.
 1. 3. 9. 4. 7. 0. 7. 9. 5. 7. 3. 5. 0. 0. 5. 6. 1. 8. 1. 5. 3. 6. 2. 8.
 3. 5. 4. 6. 3. 2. 1. 0. 5. 5. 1. 7. 1. 0. 1. 1. 6. 4. 5. 8. 0. 1. 8. 5.
 0. 7. 9. 3. 1. 9. 7. 9. 8. 9. 6. 7. 9. 0. 3. 9. 1. 6. 3. 7. 5. 5. 8. 8.
 9. 2. 5. 0. 6. 9. 0. 1. 4. 7. 6. 1. 1. 6. 9. 0. 5. 5. 5. 6. 7. 1. 6. 6.
 1. 6. 7. 0. 3. 2. 1. 4. 3. 5. 0. 1. 1. 6. 2. 0. 1. 0. 9. 4. 4. 1. 8. 4.
 2. 8. 1. 8. 3. 4. 3. 4. 3. 9. 9. 4. 7. 5. 0. 0. 2. 7. 8. 6. 2. 2. 5. 7.
 2. 5. 9. 9. 9. 2. 8. 1. 9. 8. 2. 0. 6. 7. 2. 9. 9. 2. 3. 7. 4. 8. 5. 4.
 9. 9. 9. 4. 1. 4. 1. 9. 8. 5. 6. 5. 3. 3. 6. 3. 8. 5. 8. 0. 2. 9. 0. 7.
 7. 6. 8. 5. 3. 0. 0. 7. 6. 1. 6. 3. 4. 3. 4. 2. 1. 3. 1. 4. 6. 9. 9. 5.
 0. 0. 5. 3. 0. 3. 5. 4. 3. 7. 1. 6. 5. 4. 4. 2. 5. 4. 9. 0. 2. 3. 7. 7.
 4. 1. 8. 7. 5. 4. 2. 9. 4. 4. 9. 8. 2. 7. 1. 9. 4. 2. 8. 1. 6. 2. 5. 6.
 8. 5. 2. 2. 8. 1. 1. 7.

# LOGREG

In [88]:
import numpy as np
import machine_learning.linear_models.activations as activations
import machine_learning.metrics.metrics as metrics

In [152]:
class LogRegression :
    def __init__(self):
        self.lr = 0.01
        self.coeff = None
        self.dim = None
        self.steps = 100
        self.min_error = 0.0001
        self.print_step = 10

    def fit(self, X_train:np.ndarray, y_train : np.ndarray) -> np.ndarray :
        ones = np.ones((X_train.shape[0],1))
        X = np.concatenate([ones, X_train], axis = 1)
        if len(y_train.shape) == 1 :
            y_train = np.expand_dims(y_train, axis = 1)
        #print(y_train)
        self.dim = X.shape[1]
        self.coeff = np.random.normal(loc = 0, scale = 0.1, size = (self.dim,1))

        for i in range(self.steps) :
            y_pred = self.predict(X, add_ones = False)
            if i % self.print_step  == 0 :
                acc = metrics.accuracy(y_train, y_pred)
                print('it {} acc_train {}'.format(i,acc), flush = True)

            diff = (y_train - y_pred)
            adjust = diff * X
            adjust = np.mean(adjust, axis = 0, keepdims = True)
            adjust = np.transpose(adjust)
            self.coeff = self.coeff + self.lr * adjust

        return self.coeff


    def predict(self, X: np.ndarray, add_ones = True) -> np.ndarray :
        if add_ones :
            ones = np.ones((X.shape[0],1))
            X = np.concatenate([ones, X], axis = 1)
        y_pred =  np.matmul(X, self.coeff)
        y_pred = activations.sigmoid(y_pred)
        return y_pred


# METRICS

In [163]:
#coefficient of determination
import numpy as np

def r2score(y_true, y_pred):
    mu = np.mean(y_true)
    sigma = np.sum(np.square(y_true - mu))
    sigma_r = np.sum(np.square(y_true - y_pred))
    return 1 - sigma_r / sigma

def accuracy(y_true, y_pred):
    y_pred = y_pred.copy()
    y_pred[y_pred < 0.5] = 0
    y_pred[y_pred >= 0.5] = 1
    acc = np.mean(np.equal(y_true,y_pred).astype(dtype = np.int32))
    return acc

def multiclass_accuracy(y_true, y_pred):
    y_pred = y_pred.copy()
    y_pred = np.argmax(y_pred, axis = 1, keepdims = False)
    acc = np.mean(np.equal(np.squeeze(y_true),np.squeeze(y_pred)).astype(dtype = np.int32))
    return acc

def confusion_matrix(y_true, y_pred, n_classes):
    y_pred = np.argmax(y_pred, axis = 1, keepdims = True)
    cm = np.zeros((n_classes, n_classes), dtype = np.int32)
    for cl_true in np.arange(n_classes) :
        y = y_pred[y_true == cl_true]
        for cl_pred in np.arange(n_classes) :
            cm[cl_true, cl_pred]= np.sum(y==cl_pred)
    return cm

# ACTIVATIONS

In [ ]:
#activation functions
def sigmoid(x: np.ndarray) -> np.ndarray :
    out = 1.0 / (1 + np.exp(-x))
    return out

def sigmoid_derivative(x: np.ndarray) -> np.ndarray :
    sig = sigmoid(x)
    out = sig*(1 - sig)
    return out

def softmax(x: np.ndarray, axis = 0):
    e_x = np.exp(x - np.max(x, axis = axis, keepdims = True))
    sm  = np.sum(e_x, axis = axis, keepdims = True)
    return e_x / sm

In [173]:
import random
classifiers = []

for digit in range(10):
    print(f"Training digit {digit}")
    ctr = 0
    index = 0
    data = []

    while i < 430:
        if train[index]['y'] == str(digit):
            data.append(train[index])
            ctr += 1
        index += 1
    ctr = 0
    index = 0

    while ctr < 430:
        if train[index]['y'] != str(digit):
            data.append(train[index])
            ctr += 1
        index += 1
    random.shuffle(data)

    x_train = np.array([data["x"] for data in train])
    y_train = np.array([data["y"] for data in train]).astype(np.float32)
    x_valid = np.array([data["x"] for data in valid])
    y_valid = np.array([data["y"] for data in valid]).astype(np.float32)
    print(x_train.shape)

    y_train_bin = (y_train == digit).astype(np.float64)
    model = LogRegression()
    model.fit(x_train, y_train_bin)

    x_valid = np.array([d['x'] for d in valid])
    y_valid = []

    for d_space in valid:
        if d_space['y'] == str(digit):
            y_valid.append(np.array([1]).astype(np.float64))
        else:
            y_valid.append(np.array([0]).astype(np.float64))

    y_valid = np.array(y_valid)
    y_predict = model.predict(x_valid)
    classifiers.append(accuracy(y_valid, y_predict))

print(classifiers)


Training digit 0
(5000, 784)
it 0 acc_train 0.4184


/content/machine_learning/linear_models/activations.py:4: RuntimeWarning: overflow encountered in exp
  out = 1.0 / (1 + np.exp(-x))


it 10 acc_train 0.9042
it 20 acc_train 0.9616
it 30 acc_train 0.9024
it 40 acc_train 0.9756
it 50 acc_train 0.9778
it 60 acc_train 0.9754
it 70 acc_train 0.9766
it 80 acc_train 0.9792
it 90 acc_train 0.981
Training digit 1
(5000, 784)
it 0 acc_train 0.7376
it 10 acc_train 0.7594
it 20 acc_train 0.8874
it 30 acc_train 0.8874
it 40 acc_train 0.7892
it 50 acc_train 0.9576
it 60 acc_train 0.9794
it 70 acc_train 0.9808
it 80 acc_train 0.9824
it 90 acc_train 0.9832
Training digit 2
(5000, 784)
it 0 acc_train 0.9024
it 10 acc_train 0.9024
it 20 acc_train 0.9024
it 30 acc_train 0.9024
it 40 acc_train 0.9024
it 50 acc_train 0.9024
it 60 acc_train 0.9382
it 70 acc_train 0.85
it 80 acc_train 0.9562
it 90 acc_train 0.9174
Training digit 3
(5000, 784)
it 0 acc_train 0.9014
it 10 acc_train 0.9172
it 20 acc_train 0.903
it 30 acc_train 0.9296
it 40 acc_train 0.9454
it 50 acc_train 0.927
it 60 acc_train 0.9238
it 70 acc_train 0.9502
it 80 acc_train 0.831
it 90 acc_train 0.952
Training digit 4
(5000, 78

In [172]:
'''
n_classes = 10
y_pred_all = np.zeros((x_valid.shape[0], n_classes))

for i in range(n_classes):
    y_train_bin = (y_train == i).astype(np.float64)
    model = LogRegression()
    model.fit(x_train, y_train_bin)
    y_pred_all[:, i] = model.predict(x_valid).flatten()

y_pred_final = np.argmax(y_pred_all, axis=1)
print("Accuracy:", accuracy(y_valid, y_pred_final))
cm = confusion_matrix(y_valid, y_pred_all, n_classes)
print("Confusion Matrix:\n", cm)
'''

#print(x_train.shape)
#print(y_train_bin.shape)
#430 de la clase vs 400 no de la clase (ajustar) para las train images

#hacer un histograma de la accuracy con cada dígito y la confusion matrix hacerla plot

it 0 acc_train 0.1
it 10 acc_train 0.9042
it 20 acc_train 0.9506
it 30 acc_train 0.9722
it 40 acc_train 0.975
it 50 acc_train 0.9758
it 60 acc_train 0.9762
it 70 acc_train 0.976
it 80 acc_train 0.9782
it 90 acc_train 0.9778
it 0 acc_train 0.3654
it 10 acc_train 0.8874
it 20 acc_train 0.8874
it 30 acc_train 0.8874
it 40 acc_train 0.9766
it 50 acc_train 0.9778
it 60 acc_train 0.9596
it 70 acc_train 0.8874
it 80 acc_train 0.9568
it 90 acc_train 0.9816
it 0 acc_train 0.4556
it 10 acc_train 0.9024
it 20 acc_train 0.9024
it 30 acc_train 0.9024
it 40 acc_train 0.9024
it 50 acc_train 0.8532
it 60 acc_train 0.9024
it 70 acc_train 0.9226
it 80 acc_train 0.8992
it 90 acc_train 0.95
it 0 acc_train 0.9014
it 10 acc_train 0.919
it 20 acc_train 0.9028
it 30 acc_train 0.9038
it 40 acc_train 0.945
it 50 acc_train 0.9524
it 60 acc_train 0.943
it 70 acc_train 0.9074
it 80 acc_train 0.9598
it 90 acc_train 0.9514
it 0 acc_train 0.107
it 10 acc_train 0.107
it 20 acc_train 0.893
it 30 acc_train 0.893
it 40 a

In [170]:
#llamar en accuracy para comparar (y_valid)
y_valid_bin = (y_valid == 0).astype(np.float64)
print(accuracy(y_valid_bin, model.predict(x_valid)))

0.916


In [ ]:
'''def display_plots(x_train, y_train, x_test, y_test, y_pred_train, y_pred_test, order, title=''):
    fig, ax = plt.subplots(1, 2, figsize=(12, 6))
    ax[0].set_ylim([-2, 2])
    ax[0].set_title('Training (order {})'.format(order))
    ax[1].set_ylim([-2, 2])
    ax[1].set_title('Testing  (order {})'.format(order))
    ax[0].plot(x_train, y_train, 'b')
    ax[0].plot(x_train, y_pred_train, 'r')
    ax[1].plot(x_test, y_test, 'b')
    ax[1].plot(x_test, y_pred_test, 'r')
    plt.suptitle(title)
    plt.show()
display_plots(x_train, y_train_noisy, x_test, y_test, y_pred_train, y_pred_test, order, title='Logistic Regression')'''

# HOG

In [ ]:
import tensorflow.keras.datasets as datasets
import matplotlib.pyplot as plt
import numpy as np
from skimage.feature import hog


def getSample(n_rows, n_cols, data):
    size = 28
    image = np.ones((n_rows*size, n_cols*size), dtype = np.uint8)*255
    n = n_rows * n_cols
    idx = np.random.randint(data.shape[0], size = n)

    i = 0
    for r in np.arange(n_rows) :
            for c in np.arange(n_cols) :
                image[r * size:(r + 1) * size, c * size : (c + 1) * size] = data[idx[i], : , : ]
                i = i + 1

    return image

if __name__ == '__main__' :
    (x_train, y_train), (x_test, y_test) = datasets.mnist.load_data()
    print ('{} {}'.format(x_train.shape, x_train.dtype))
    print ('{} {}'.format(x_test.shape, x_train.dtype))
    digit = x_train[10,:,:];
    print(digit.shape)
    fd, hog_image = hog(digit, orientations=8, pixels_per_cell=(7,7),
                    cells_per_block=(1, 1), visualize=True)
    print(fd)
    fig, xs = plt.subplots(1,2)
    xs[0].imshow(digit, cmap = 'gray')
    xs[1].imshow(hog_image, cmap = 'gray')
    print(fd.shape)
    # image = getSample(10,20, x_train)
    #plt.imshow(image, cmap = 'gray')
    # plt.axis('off')
    plt.show()

